In [13]:
import os
import pandas as pd
import numpy as np
import sys

from dotenv import load_dotenv
from openai import AzureOpenAI

from langchain_openai import AzureChatOpenAI
from langchain_core.messages import HumanMessage

import csv
import json
import time
from datetime import date, datetime


from langchain_openai import AzureChatOpenAI
import tiktoken


print('Python version:', sys.version)
print('Python executable:', sys.executable)
print('pandas version:', pd.__version__)
print('\nCurrent working directory:', os.getcwd())

Python version: 3.12.11 | packaged by Anaconda, Inc. | (main, Jun  5 2025, 12:58:53) [MSC v.1929 64 bit (AMD64)]
Python executable: c:\Users\Denis_Davydov2\AppData\Roaming\pypoetry\venv\Scripts\python.exe
pandas version: 2.3.3

Current working directory: c:\Users\Denis_Davydov2\OneDrive\Scipts\Py_Scripts\EPAM\Prophet\AI_skills\Ver_2


# Get skills defenition and texts

In [14]:
# Get skills list
file_path = 'C:\\Users\\Denis_Davydov2\\OneDrive - EPAM\\Prophet_AI_docs\\Datasets\\AI_skills\\Clusters\\'
file_name = 'Skills_with_names_2025-11-12.csv'
skills = pd.read_csv(file_path+file_name)
print("File read: ", file_name)

skills = skills[['cluster_id', 'skill_name', 'skill_definition']]
skills
skills['skill'] = skills['skill_name'] + ":\n" + skills['skill_definition']
skills


# Add token count column
def num_tokens_from_string(string, encoding_name):
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(string if isinstance(string, str) else '', disallowed_special=()))
    return num_tokens

skills['token_count'] = skills['skill'].apply(lambda text: num_tokens_from_string(text, "cl100k_base"))
skills = skills[skills['token_count']>0]

print("Total tokens:", skills['token_count'].sum())
print("Min tokens:", skills['token_count'].min())
print("Max tokens:", skills['token_count'].max())
skills

File read:  Skills_with_names_2025-11-12.csv
Total tokens: 10824
Min tokens: 50
Max tokens: 140


cluster_id                              skill_name  \
0             0             LLM Application Engineering   
1             1               Alexa and AWS Development   
2             2                    AI Agent Engineering   
3             6                     AI Data Engineering   
4             7  Model Quantization and Mixed Precision   
..          ...                                     ...   
139         136        MCP Server and Agent Development   
140         135         Low-code No-code AI Development   
141         141                AI Model Risk Management   
142         137        GAN Development and Optimization   
143         138               Serverless AI Engineering   

                                      skill_definition  \
0    Design, build, and deploy LLM-powered applicat...   
1    Design, build, and deploy Alexa skills and voi...   
2    Design, program, and deploy autonomous AI agen...   
3    Ability to design, build, and manage scalable ...   
4    Ability to design, implement, and optimize low...   
..                                                 ...   
139  Build and integrate MCP servers and agents tha...   
140  Build and deploy AI/ML applications and automa...   
141  Ability to assess, quantify, prioritize, and m...   
142  Design, implement, and train GAN variants (cGA...   
143  Design, deploy, and optimize ML and RL workloa...   

                                                 skill  token_count  
0    LLM Application Engineering:\nDesign, build, a...           66  
1    Alexa and AWS Development:\nDesign, build, and...          140  
2    AI Agent Engineering:\nDesign, program, and de...           60  
3    AI Data Engineering:\nAbility to design, build...           57  
4    Model Quantization and Mixed Precision:\nAbili...          101  
..                                                 ...          ...  
139  MCP Server and Agent Development:\nBuild and i...           59  
140  Low-code No-code AI Development:\nBuild and de...           62  
141  AI Model Risk Management:\nAbility to assess, ...           61  
142  GAN Development and Optimization:\nDesign, imp...           75  
143  Serverless AI Engineering:\nDesign, deploy, an...           65  

[144 rows x 5 columns]

In [15]:
# Get texts
file_path = 'C:\\Users\\Denis_Davydov2\\OneDrive - EPAM\\Prophet_AI_docs\\Datasets\\AI_skills\\'
file_name = 'smolai_texts_cleaned_2025-11-14.csv'


smalai = pd.read_csv(file_path+file_name)
print("File read: ", file_name)


tokens_total = smalai['token_count'].sum()
print("Total tokens", tokens_total)
print("Min tokens:", smalai['token_count'].min())
print("Max tokens:", smalai['token_count'].max())

smalai['text_id'] = smalai.index

smalai['summary'] = "text ID: " +smalai['text_id'].astype(str) + "\n" + smalai['content_deduped']


smalai

File read:  smolai_texts_cleaned_2025-11-14.csv
Total tokens 2030998
Min tokens: 808
Max tokens: 9760


title  issue_date  \
0    Cursor 2.0 & Composer-1: Fast Models and New A...  2025-10-29   
1    OpenAI completes Microsoft + For-profit restru...  2025-10-28   
2    MiniMax M2 230BA10B â 8% of Claude Sonnet's ...  2025-10-27   
3                              not much happened today  2025-10-24   
4                              not much happened today  2025-10-23   
..                                                 ...         ...   
408                      Terminal-Bench 2.0 and Harbor  2025-11-07   
409                            not much happened today  2025-11-10   
410                            not much happened today  2025-11-11   
411  GPT 5.1 in ChatGPT: No evals, but adaptive thi...  2025-11-12   
412                            not much happened today  2025-11-04   

                                       content_deduped  token_count  text_id  \
0    Open-weight safety models and moderation tooli...         4359        0   
1    OpenAIs new structure, Microsoft deal, and ope...         5932        1   
2    MiniMax M2 open-weights release: sparse MoE fo...         5143        2   
3    Serving and Production Platforms: vLLM x NVIDI...         4863        3   
4    Agent ops, observability, and real-world envs\...         4366        4   
..                                                 ...          ...      ...   
408  Moonshot AIs Kimi K2 Thinking: 1T INT4 open-we...         5912      408   
409  Moonshot AIs Kimi K2 Thinking: AMA takeaways, ...         6322      409   
410  Reasoning benchmarks and training techniques\n...         6221      410   
411  Autonomy and Physical AI: Waymo freeway rollou...         4925      411   
412  Compute, energy, and AI datacenters\nGoogles P...         4139      412   

                                               summary  
0    text ID: 0\nOpen-weight safety models and mode...  
1    text ID: 1\nOpenAIs new structure, Microsoft d...  
2    text ID: 2\nMiniMax M2 open-weights release: s...  
3    text ID: 3\nServing and Production Platforms: ...  
4    text ID: 4\nAgent ops, observability, and real...  
..                                                 ...  
408  text ID: 408\nMoonshot AIs Kimi K2 Thinking: 1...  
409  text ID: 409\nMoonshot AIs Kimi K2 Thinking: A...  
410  text ID: 410\nReasoning benchmarks and trainin...  
411  text ID: 411\nAutonomy and Physical AI: Waymo ...  
412  text ID: 412\nCompute, energy, and AI datacent...  

[413 rows x 6 columns]

In [16]:
skills_list="\n\n".join(skills['skill'].tolist())
print(skills_list)

LLM Application Engineering:
Design, build, and deploy LLM-powered applications and agents by defining architectures, integrating APIs, and implementing toolchains for code and multimodal use cases. Select and customize models via fine-tuning or efficient training, benchmark and align them, and optimize cost, latency, and throughput for reliable production operation.

Alexa and AWS Development:
Design, build, and deploy Alexa skills and voice experiences using ASK/AVS, integrating AWS services like API Gateway, Cognito, DynamoDB, Kinesis, Lex, Polly, Kendra, Nova, and Comprehend Medical with backends on EC2/ECS/EKS and data stores such as DocumentDB and Neptune. Implement secure authentication, event-driven architectures with EventBridge, streaming and analytics via Athena and EMR, monitoring and delivery with CloudWatch and CloudFront, caching with ElastiCache, container images in ECR, and storage using EBS/EFS/FSx for Lustre, applying A2I and Neptune ML where appropriate.

AI Agent E

# Skills labeling by LLM

In [17]:
summary_texts = smalai[['summary']].copy()
#summary_texts = summary_texts.head(3)

# select rows from ...
#summary_texts = summary_texts.iloc[80:]
summary_texts


summary
0    text ID: 0\nOpen-weight safety models and mode...
1    text ID: 1\nOpenAIs new structure, Microsoft d...
2    text ID: 2\nMiniMax M2 open-weights release: s...
3    text ID: 3\nServing and Production Platforms: ...
4    text ID: 4\nAgent ops, observability, and real...
..                                                 ...
408  text ID: 408\nMoonshot AIs Kimi K2 Thinking: 1...
409  text ID: 409\nMoonshot AIs Kimi K2 Thinking: A...
410  text ID: 410\nReasoning benchmarks and trainin...
411  text ID: 411\nAutonomy and Physical AI: Waymo ...
412  text ID: 412\nCompute, energy, and AI datacent...

[413 rows x 1 columns]

In [19]:
# Prompt template function that will be called for each text

def create_prompt(text: str, skills_list: str) -> str:
    """
    Create a prompt for the LLM to identify AI skills in the given text.
    
    Args:
        text: The summary text to analyze
        skills_list: Formatted string of all AI skills with definitions
    
    Returns:
        Formatted prompt string
    """
    prompt = f"""
You will be provided with:
- AI news summary text;
- List of 144 AI-related skills used in development, deployment, governance, operations, productization, and applied data science. The first phrase before the colon is the skill name, followed by the skill definition.

Goal: Find out which of these 144 AI skills are mentioned in the news summary text.

Please review the news summary and determine if there is anything related to this AI skill set in the text
Identify in the text all the skills from the AI skills set given to you that may make sense in the context of the news summary.

OUTPUT MUST BE ONLY JSON (enforced separately). DO NOT include explanations here.

Schema (each object):
- Text ID  (get from the top of the text)
- Skill name (get from the AI skills list; Skill name only, without definition or commentary.)
- Confirmation (Quote from the text: 1 sentence where the skill is mentioned)

Rules:
- Use every skill exactly once (If a skill appears multiple times, list it once and use the text citation that most closely matches the skill's definition.).
- Only list the skill's name (do not correct or add anything)
- If no AI-related  skills are found in the text, return 'None'

AI skill list:
{skills_list}



AI news summary text
{text}
"""
    return prompt

print("Prompt template function created")

Prompt template function created


In [7]:
# === Load Environment Variables ===
load_dotenv()  # Loads variables from .env file into environment

# Retrieve database connection parameters from environment variables
DIAL_API_KEY = os.getenv('DIAL_API_KEY')

#print(DIAL_API_KEY)

In [20]:
# Process all rows from summary_texts dataframe
import json
from typing import List, Dict

# Initialize the Azure OpenAI model
model = AzureChatOpenAI(
    azure_endpoint="https://ai-proxy.lab.epam.com",
    api_key=DIAL_API_KEY,
    api_version="2025-04-01-preview",
    #model='anthropic.claude-v3-5-haiku'
    #model='anthropic.claude-haiku-4-5-20251001-v1:0'
    #model='anthropic.claude-haiku-4-5-20251001-v1:0-with-thinking'
    #model='meta.llama4-maverick-17b-instruct-v1:0'
    model='gpt-4.1-mini-2025-04-14'
)

# Refined system directive: strict JSON, target schema
system_instructions = (
    "You are an expert AI skills classifier. "
    "Task: Identify in the text all the skills from the AI skills set given to you that may make sense in the context of the news summary. "
    "Return ONLY a valid JSON array (UTF-8) with objects of this exact schema: \n"
    "[\n  {\n    \"text_id\": \"int\",       // Text ID from the top of the text\n    \"skill_name\": \"string\",       // Skill name from the AI skills list\n    \"confirmation\": \"string\"       // Quote from the text: 1-2 sentences where the skill is explicitly mentioned\n  }\n] \n"
    "\n"
    "Requirements: \n"
    "- Use every skill exactly once (If a skill appears multiple times, list it once and use the text citation that most closely matches the skill's definition.) \n"
    "- Repeat the search for each skill from the list of AI-related skills \n"
    "- Do NOT include definitions or summaries; only the three specified keys. \n"
    "- Use only double quotes for JSON; no trailing commas. \n"
    "- Exclude commentary, explanations, markdown, or code fences. Output MUST start with '[' and end with ']'. \n"
    "- If no AI-related skills are found in the text, return 'None'"
)

# Helper function to extract JSON from LLM response
def extract_json(text: str) -> str:
    """Extract JSON array from LLM response, handling markdown code blocks."""
    if text.startswith('```'):
        parts = text.split('```')
        if len(parts) >= 2:
            text = parts[1]
            # Remove language identifier (e.g., 'json')
            if text.startswith('json'):
                text = text[4:]
    start = text.find('[')
    end = text.rfind(']')
    if start != -1 and end != -1 and end > start:
        return text[start:end+1]
    raise ValueError('JSON array delimiters not found in model output.')

# Process each row
all_results = []
total_rows = len(summary_texts)
save_interval = 10  # Save results every 10 texts

print("=" * 80)
print(f"PROCESSING {total_rows} TEXTS")
print(f"Auto-save interval: every {save_interval} texts")
print("=" * 80)

ts_start = datetime.now()
print(f'Start time: {ts_start}\n')

processed_count = 0

for idx, row in summary_texts.iterrows():
    text = row['summary']
    
    print(f"Processing text {idx + 1}/{total_rows}...", end=' ')
    row_start = time.time()
    
    # Create prompt for this specific text
    prompt = create_prompt(text, skills_list)
    
    # Build messages for chat model
    messages = [
        ("system", system_instructions),
        ("human", prompt),
    ]
    
    try:
        # Invoke model
        output = model.invoke(messages)
        raw_response = output.content.strip()
        
        # Parse JSON response
        try:
            json_str = extract_json(raw_response)
            data = json.loads(json_str)
            
            # Handle special cases
            if isinstance(data, str) and data.lower() == 'none':
                data = []
            elif isinstance(data, list):
                # Filter out 'None' responses
                data = [item for item in data if not (isinstance(item, str) and item.lower() == 'none')]
            
            all_results.extend(data)
            processed_count += 1
            print(f"✓ Found {len(data)} skills ({time.time() - row_start:.1f}s) | Processed {processed_count}/{total_rows} texts")
            
        except Exception as e:
            print(f"⚠ JSON parse error: {e} ({time.time() - row_start:.1f}s)")
            # Try secondary cleanup
            cleaned = raw_response.replace('\n', ' ').replace('\r', ' ').strip('`')
            try:
                json_str = extract_json(cleaned)
                data = json.loads(json_str)
                all_results.extend(data)
                processed_count += 1
                print(f"  → Recovered {len(data)} skills after cleanup | Processed {processed_count}/{total_rows} texts")
            except Exception as e2:
                print(f"  → Failed to recover: {e2} | Processed {processed_count}/{total_rows} texts")
                print(f"  → Raw response preview: {raw_response[:200]}...")
    
    except Exception as e:
        print(f"✗ LLM invocation error: {e} ({time.time() - row_start:.1f}s) | Processed {processed_count}/{total_rows} texts")
    
    # Auto-save results every save_interval texts
    if processed_count > 0 and (processed_count % save_interval == 0 or processed_count == total_rows):
        df_temp = pd.DataFrame(all_results)
        if len(df_temp) > 0:
            required_cols = ['text_id', 'skill_name', 'confirmation']
            for col in required_cols:
                if col not in df_temp.columns:
                    df_temp[col] = None
            df_temp = df_temp[required_cols]
            
            # Save to variable for recovery
            df_checkpoint = df_temp.copy()
            print(f"💾 Auto-saved: {len(df_checkpoint)} skills from {processed_count} texts")

ts_end = datetime.now()
print(f"\n{'=' * 80}")
print(f"Processing complete")
print(f"Total time: {ts_end - ts_start}")
print(f"Total skills extracted: {len(all_results)}")
print("=" * 80)

# Convert to DataFrame
required_cols = ['text_id', 'skill_name', 'confirmation']
df_skills = pd.DataFrame(all_results)

# Ensure required columns exist
for col in required_cols:
    if col not in df_skills.columns:
        df_skills[col] = None

df_skills = df_skills[required_cols]

print(f"\nResulting DataFrame shape: {df_skills.shape}")
print(f"Unique texts: {df_skills['text_id'].nunique()}")
print(f"Unique skills: {df_skills['skill_name'].nunique()}")

display(df_skills.head(20))
df_skills

PROCESSING 413 TEXTS
Auto-save interval: every 10 texts
Start time: 2025-11-19 12:03:50.352671

Processing text 1/413... ✓ Found 18 skills (18.9s) | Processed 1/413 texts
Processing text 2/413... ✓ Found 142 skills (86.9s) | Processed 2/413 texts
Processing text 3/413... ✓ Found 20 skills (13.1s) | Processed 3/413 texts
Processing text 4/413... ✓ Found 17 skills (19.5s) | Processed 4/413 texts
Processing text 5/413... ✓ Found 25 skills (23.6s) | Processed 5/413 texts
Processing text 6/413... ✓ Found 27 skills (20.6s) | Processed 6/413 texts
Processing text 7/413... ✓ Found 13 skills (10.9s) | Processed 7/413 texts
Processing text 8/413... ✓ Found 28 skills (15.2s) | Processed 8/413 texts
Processing text 9/413... ✓ Found 78 skills (49.2s) | Processed 9/413 texts
Processing text 10/413... ✓ Found 135 skills (76.9s) | Processed 10/413 texts
💾 Auto-saved: 503 skills from 10 texts
Processing text 11/413... ✓ Found 21 skills (19.6s) | Processed 11/413 texts
Processing text 12/413... ✓ Found 

text_id                              skill_name  \
0        0                    AI Agent Engineering   
1        0  Model Quantization and Mixed Precision   
2        0                     AI Data Engineering   
3        0      Reinforcement Learning Engineering   
4        0             LLM Application Engineering   
5        0            Generative Media Engineering   
6        0                    Cloud AI Engineering   
7        0          AI Evaluation and Benchmarking   
8        0                 AI Security Engineering   
9        0                    AI Model Fine-Tuning   
10       0                AI Safety and Governance   
11       0                      AI Model Debugging   
12       0                   AI Process Automation   
13       0                      AI API Engineering   
14       0              AI Reliability Engineering   
15       0                   AI Content Moderation   
16       0         AI Model Serving and Deployment   
17       0             AI Strategy and Integration   
18       1                    AI Agent Engineering   
19       1                     AI Data Engineering   

                                         confirmation  
0   Composer1 (agentic coding model) : Major IDE u...  
1   Cheaper alternative to LLM-as-judge : Goodfire...  
2   Agent Data Protocol (ADP) : A unified, open st...  
3   Composer1 is an RLtrained MoE optimized for sp...  
4   OpenAIs gpt-oss-safeguard (20B, 120B) : Two op...  
5   FIBO (Bria) 8B image model (open weights) : Tr...  
6   AWS detailed a large Trainium2 clusternearly 5...  
7   ImpossibleBench Catches GPT-5 Red-Handed: A ne...  
8   Ollama Vulnerability Exposes 10,000 Servers: A...  
9   Thinking Machines Flips the Script on LoRA: Th...  
10  OpenAI asserts it has implemented safeguards l...  
11  Discussions highlighted confusion in the spec ...  
12  LangSmith Agent Builder (LangChain) : Nocode b...  
13  APIs Mysteriously Remove Control Levers: Devel...  
14  Cursor users are seeing excessive token usage,...  
15  Open-weight safety models and moderation tooli...  
16  The rollout included a hackathon and the ROOST...  
17  OpenAI org/roadmap and Sora app : Sam Altman o...  
18  GitHub Agent HQ and VS Code Agent Sessions: Gi...  
19  LeRobot v0.4 ships a streamable dataset format...

text_id                              skill_name  \
0           0                    AI Agent Engineering   
1           0  Model Quantization and Mixed Precision   
2           0                     AI Data Engineering   
3           0      Reinforcement Learning Engineering   
4           0             LLM Application Engineering   
...       ...                                     ...   
14152     412                AI Safety and Governance   
14153     412      Distributed Training and Inference   
14154     412                    Cloud AI Engineering   
14155     412             AI Strategy and Integration   
14156     412     Experimentation and Test Automation   

                                            confirmation  
0      Composer1 (agentic coding model) : Major IDE u...  
1      Cheaper alternative to LLM-as-judge : Goodfire...  
2      Agent Data Protocol (ADP) : A unified, open st...  
3      Composer1 is an RLtrained MoE optimized for sp...  
4      OpenAIs gpt-oss-safeguard (20B, 120B) : Two op...  
...                                                  ...  
14152  The paper warning against AI developing commun...  
14153  Tritex repo enabled from-scratch LLM pre-train...  
14154  Debates raged on Tinybox Pro V2's value versus...  
14155  Discussions about EU AI Act hindering Western ...  
14156  Epoch AI slammed the OSWorld benchmark for sim...  

[14157 rows x 3 columns]

In [31]:
# Test connection
model = AzureChatOpenAI(
    openai_api_version="2025-04-01-preview",
    azure_deployment="claude-haiku-4-5@20251001",
    azure_endpoint="https://ai-proxy.lab.epam.com",
    api_key=DIAL_API_KEY
)

response = model.invoke(
    [
        HumanMessage(
            content="This is a test!"
        )
    ]
)
print(response.content)

InternalServerError: Error code: 500 - {'error': {'message': 'Streaming is strongly recommended for operations that may take longer than 10 minutes. See https://github.com/anthropics/anthropic-sdk-python#long-requests for more details', 'type': 'internal_server_error', 'code': '500'}}

In [21]:
df_skills

text_id                              skill_name  \
0           0                    AI Agent Engineering   
1           0  Model Quantization and Mixed Precision   
2           0                     AI Data Engineering   
3           0      Reinforcement Learning Engineering   
4           0             LLM Application Engineering   
...       ...                                     ...   
14152     412                AI Safety and Governance   
14153     412      Distributed Training and Inference   
14154     412                    Cloud AI Engineering   
14155     412             AI Strategy and Integration   
14156     412     Experimentation and Test Automation   

                                            confirmation  
0      Composer1 (agentic coding model) : Major IDE u...  
1      Cheaper alternative to LLM-as-judge : Goodfire...  
2      Agent Data Protocol (ADP) : A unified, open st...  
3      Composer1 is an RLtrained MoE optimized for sp...  
4      OpenAIs gpt-oss-safeguard (20B, 120B) : Two op...  
...                                                  ...  
14152  The paper warning against AI developing commun...  
14153  Tritex repo enabled from-scratch LLM pre-train...  
14154  Debates raged on Tinybox Pro V2's value versus...  
14155  Discussions about EU AI Act hindering Western ...  
14156  Epoch AI slammed the OSWorld benchmark for sim...  

[14157 rows x 3 columns]

In [11]:
df_checkpoint

text_id                            skill_name  \
0          0           LLM Application Engineering   
1          0         Conversational AI Engineering   
2          0                  AI Agent Engineering   
3          0  Hugging Face Transformer Engineering   
4          0                  AI Model Fine-Tuning   
...      ...                                   ...   
2530     271  AI Performance and Cost Optimization   
2531     271       AI Model Serving and Deployment   
2532     271              AI Inference Engineering   
2533     271         Efficient Sequence Generation   
2534     271             Multimodal AI Engineering   

                                           confirmation  
0     Open-weight safety models and moderation tooli...  
1     Cursor 2.0 and Composer1 (agentic coding model...  
2     Agent Data Protocol (ADP) : A unified, open st...  
3     MiniMaxM2 momentum : Global developer enthusia...  
4     Marin 32B Base (mantis) : Open lab release cla...  
...                                                 ...  
2530  person_1331 shared a resource on building a go...  
2531  person_1011 announced OpenAI Secures $6.6 Bill...  
2532  person_1332 shared insights on the DMC paper ,...  
2533  person_1333 highlighted the benefits of ZeRO++...  
2534  person_1340 shared the paper , proposing adapt...  

[2535 rows x 3 columns]

In [22]:
file_path = r'C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Skills_dynamics'
file_name = f'gpt41mini.csv'

df_skills.to_csv(file_path + '\\' + file_name, index=False, encoding='utf-8-sig')
print(f"File {file_name} \nuploaded to:", file_path)


File gpt41mini.csv 
uploaded to: C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Skills_dynamics
